# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with `YOUR IMPORT TEXT HERE`

In [1]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [2]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [3]:
# confirm that our new database was created
print(mongo.list_database_names())

['admin', 'autosaurus', 'classDB', 'config', 'epa', 'fruits_db', 'local', 'met', 'myDatabase', 'petsitly_marketing', 'travel_db', 'uk_food']


In [4]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [5]:
# review the collections in our new database
print(db.list_collection_names())

['establishments']


In [6]:
# review a document in the establishments collection
pprint(db.establishments.find_one())

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('66e978a75267aa8855a63ad4'),
 'geocode': {'latitude': '51.083812', 'longitude': '1.195625'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': No

In [7]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [8]:
# Create a dictionary for the new restaurant data
new_restaurant = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [9]:
# Insert the new restaurant into the collection
establishments.insert_one(new_restaurant)

InsertOneResult(ObjectId('66ea11df59516016406b2539'), acknowledged=True)

In [30]:
# Check that the new restaurant was inserted
pprint(establishments.find_one(
    {"BusinessName":"Penang Flavours"}
))

{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'Distance': 4623.972328074718,
 'LocalAuthorityCode': '511',
 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
 'LocalAuthorityName': 'Greenwich',
 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
 'NewRatingPending': True,
 'Phone': '',
 'PostCode': 'SE18 7DY',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('66e97db0c0e83a0f89fd91f5'),
 'geocode': {'latitude': '51.49014200', 'longitude': '0.08384000'},
 'scores': {'ConfidenceInManagement': '', 'Hygiene': '', 'Structural': ''}}


2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [29]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and 
# return only the BusinessTypeID and BusinessType fields
pprint(establishments.find_one(
    {"BusinessType": "Restaurant/Cafe/Canteen"},
    {"BusinessTypeID": 1, "BusinessType": 1}
))

{'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 '_id': ObjectId('66e978a75267aa8855a63ad4')}


3. Update the new restaurant with the `BusinessTypeID` you found.

In [12]:
# Update the new restaurant with the correct BusinessTypeID
filter_query = {"BusinessName": "Penang Flavours"}
establishments.update_one(
    filter_query,
    {"$set": {"BusinessTypeID": 1}}
)

UpdateResult({'n': 1, 'nModified': 0, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [28]:
# Confirm that the new restaurant was updated
print(establishments.find_one(
    {"BusinessName": "Penang Flavours"},
    {"BusinessTypeID": 1}
))

{'_id': ObjectId('66e97db0c0e83a0f89fd91f5'), 'BusinessTypeID': 1}


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [24]:
# Find how many documents have LocalAuthorityName as "Dover"
print(establishments.count_documents({"LocalAuthorityName": "Dover"}))

0


In [15]:
# Delete all documents where LocalAuthorityName is "Dover"
establishments.delete_many({"LocalAuthorityName": "Dover"})

DeleteResult({'n': 0, 'ok': 1.0}, acknowledged=True)

In [25]:
# Check if any remaining documents include Dover
print(establishments.count_documents({"LocalAuthorityName": "Dover"}))

0


In [27]:
# Check that other documents remain with 'find_one'
pprint(establishments.find_one())

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('66e978a75267aa8855a63ad4'),
 'geocode': {'latitude': '51.083812', 'longitude': '1.195625'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': No

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [18]:
# Change the data type from String to Decimal for longitude and latitude
establishments.update_many(
    filter={"longitude": {"$type": "string"}},
    update=[{"$set": {"longitude": {"$toInt": "$longitude"}}}]
)

establishments.update_many(
    filter={"latitude": {"$type": "string"}},
    update=[{"$set": {"latitude": {"$toInt": "$latitude"}}}]
)

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

Use `update_many` to convert `RatingValue` to integer numbers.

In [19]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

In [20]:
# Change the data type from String to Integer for RatingValue
establishments.update_many(
    filter={"RatingValue": {"$type": "string"}},
    update=[{"$set": {"RatingValue": {"$toInt": "$RatingValue"}}}]
)

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

In [21]:
# Check that the coordinates and rating value are now numbers
longitude = [
    {
        "$project": {
            "fieldTypes": { "$type": "$longitude" }
        }
    }
]
result = establishments.aggregate(longitude)

for doc in result:
    print(doc)

{'_id': ObjectId('66e978a75267aa8855a63ad4'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ad6'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ad7'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63adb'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63add'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ade'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63adf'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae0'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae2'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae3'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae5'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae7'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae8'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae9'), 'fieldTypes': 'missing'}
{'_id'

In [22]:
pipeline = [
    {
        "$project": {
            "fieldTypes": { "$type": "$latitude" }
        }
    }
]
result = establishments.aggregate(pipeline)

for doc in result:
    print(doc)

{'_id': ObjectId('66e978a75267aa8855a63ad4'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ad6'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ad7'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63adb'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63add'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ade'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63adf'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae0'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae2'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae3'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae5'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae7'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae8'), 'fieldTypes': 'missing'}
{'_id': ObjectId('66e978a75267aa8855a63ae9'), 'fieldTypes': 'missing'}
{'_id'

In [23]:
pipeline = [
    {
        "$project": {
            "fieldTypes": { "$type": "$RatingValue" }
        }
    }
]
result = establishments.aggregate(pipeline)

for doc in result:
    print(doc)

{'_id': ObjectId('66e978a75267aa8855a63ad4'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ad6'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ad7'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63adb'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63add'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ade'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63adf'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae0'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae2'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae3'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae5'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae7'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae8'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63ae9'), 'fieldTypes': 'int'}
{'_id': ObjectId('66e978a75267aa8855a63aea'), 'fieldTypes': 'i